# Import libraries

In [1]:
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
import numpy as np
#import sklearn
plt.style.use('bmh')

# 01 Read in Data

In [2]:
#A. Read in Main file
#filepath = "../Data/mergedSample.csv"
filepath = "../Data/final_merged.csv"
data = pd.read_csv(filepath)
data = data.rename(columns = {"demand": "mw", "avg": "tempf"})
del data['Unnamed: 0']

data.head()

datetime      mw  abbr         datetime_utc        date  hour  \
0  2018-10-20 17:00:00  3707.0  AZPS  2018-10-21 00:00:00  2018-10-20    17   
1  2018-10-20 16:00:00  3586.0  AZPS  2018-10-20 23:00:00  2018-10-20    16   
2  2018-10-20 15:00:00  3395.0  AZPS  2018-10-20 22:00:00  2018-10-20    15   
3  2018-10-20 01:00:00  2608.0  AZPS  2018-10-20 08:00:00  2018-10-20     1   
4  2018-10-20 00:00:00  2737.0  AZPS  2018-10-20 07:00:00  2018-10-20     0   

    tempf  
0  69.260  
1  67.055  
2  64.130  
3  71.285  
4  74.570

In [3]:
#B. Read in system info
filepath = "../Data/operating_system_names_and_info.csv"
systeminfo = pd.read_csv(filepath)
systeminfo =  systeminfo[['ID', 'NAME', 'abbrev','PEAK_MONTH', 'AVAIL_CAP',
       'TOTAL_CAP', 'PEAK_LOAD', 'MIN_LOAD', 'SHAPE__Are', 'lat', 'lon']]
systeminfo.rename(columns = {'abbrev': 'abbr'}, inplace = True)
systeminfo.head()

ID                                        NAME  abbr  PEAK_MONTH  \
0    803              ARIZONA PUBLIC SERVICE COMPANY  AZPS         6.0   
1    924       ASSOCIATED ELECTRIC COOPERATIVE, INC.  AECI        12.0   
2  20169                          AVISTA CORPORATION   AVA        12.0   
3  16534  BALANCING AUTHORITY OF NORTHERN CALIFORNIA  BANC         7.0   
4   1738             BONNEVILLE POWER ADMINISTRATION  BPAT        12.0   

   AVAIL_CAP  TOTAL_CAP  PEAK_LOAD  MIN_LOAD    SHAPE__Are         lat  \
0    71475.0    90516.0     7275.0    2260.0  4.171880e+11 -111.569906   
1    61242.0    73752.0     4521.0    1143.0  4.359740e+11  -93.391195   
2    27943.0    28843.0     2273.0     961.0  2.487650e+11 -116.905492   
3    43244.0    53053.0     4426.0    2183.0  5.469669e+10 -121.899037   
4   254766.0   478749.0     9739.0    4105.0  1.419380e+12 -117.424931   

         lon  
0  34.316049  
1  37.987117  
2  47.039167  
3  39.657983  
4  44.868673

In [4]:
data.head()

datetime      mw  abbr         datetime_utc        date  hour  \
0  2018-10-20 17:00:00  3707.0  AZPS  2018-10-21 00:00:00  2018-10-20    17   
1  2018-10-20 16:00:00  3586.0  AZPS  2018-10-20 23:00:00  2018-10-20    16   
2  2018-10-20 15:00:00  3395.0  AZPS  2018-10-20 22:00:00  2018-10-20    15   
3  2018-10-20 01:00:00  2608.0  AZPS  2018-10-20 08:00:00  2018-10-20     1   
4  2018-10-20 00:00:00  2737.0  AZPS  2018-10-20 07:00:00  2018-10-20     0   

    tempf  
0  69.260  
1  67.055  
2  64.130  
3  71.285  
4  74.570

In [5]:
pd.set_option('display.float_format', lambda x: '%.1f' % x)
data.describe()

mw      hour     tempf
count    1148864.0 1148864.0 1141478.0
mean       15063.6      11.6      60.2
std      2470843.9       6.9      18.2
min    -99913317.0       0.0     -20.8
25%          843.0       6.0      47.6
50%         2410.0      12.0      61.2
75%         5932.0      18.0      74.3
max   1000001946.0      23.0     112.1

In [6]:
data['datetime'] = pd.to_datetime(data.datetime)  # Convert to datetime object
data.datetime.asfreq("H")  #  informs data is hourly

1970-01-01   NaT
Freq: H, Name: datetime, dtype: datetime64[ns]

In [7]:
#C. Summarize dataset info
print(data.columns)
data.describe()

Index(['datetime', 'mw', 'abbr', 'datetime_utc', 'date', 'hour', 'tempf'], dtype='object')


mw      hour     tempf
count    1148864.0 1148864.0 1141478.0
mean       15063.6      11.6      60.2
std      2470843.9       6.9      18.2
min    -99913317.0       0.0     -20.8
25%          843.0       6.0      47.6
50%         2410.0      12.0      61.2
75%         5932.0      18.0      74.3
max   1000001946.0      23.0     112.1

# Define Features

In [8]:
#A. Extract additional time variables 

data['year'] = data['datetime'].dt.year
data['month'] = data['datetime'].dt.month
data['dayofweek'] = data['datetime'].dt.dayofweek
data['dayofyear'] = data['datetime'].dt.dayofyear
data['date'] = data['datetime'].dt.date
data['hour'] = data['datetime'].dt.hour   
data['weekday'] = (0< data['dayofweek']) &  (data['dayofweek'] <6)

In [9]:
data['weekday'].value_counts()

True     822660
False    326204
Name: weekday, dtype: int64

In [10]:
#B. Extract peak and average info

dategroup = data.groupby(by = 'date')
#data = dategroup.mw.mean()
data = data.join(data.groupby(['abbr','date'])['mw'].max(), on =['abbr','date'], rsuffix='_avg')
data = data.join(data.groupby(['abbr','date'])['mw'].max(), on = ['abbr','date'], rsuffix='_peak')
data = data.join(data.groupby(['abbr','date'])['tempf'].max(), on = ['abbr','date'], rsuffix='_peak')
data = data.join(data.groupby(['abbr','date'])['tempf'].mean(), on = ['abbr','date'], rsuffix='_avg')

In [11]:
#C. Extract lags for weather and MW
data.set_index(["abbr", "datetime"], inplace = True) # Set as index for lags
data['mw_3hrlag'] = data.mw.shift(3)
data['mw_24hrlag'] = data.mw.shift(24)
data['mw_weeklag'] = data.mw.shift(168)
data['tempf_3hrlag'] = data.tempf.shift(3)
data['tempf_24hrlag'] = data.tempf.shift(24)
data['tempf_weeklag'] = data.tempf.shift(168)


In [12]:
# Create Traditional weather variable

# CDD
data['cdd60_temp'] =  data['tempf_avg'] -60
data['zero'] = 0 
data['cdd60'] = data[['zero', 'cdd60_temp']].max(axis=1)
del data['cdd60_temp']

# HDD 
data['hdd60_temp'] =  data['tempf_avg'] -60
data['hdd60'] = data[['zero', 'hdd60_temp']].max(axis=1)
del data['hdd60_temp']

# CDH
data['cdh60_temp'] =  data['tempf']-60
data['cdh60'] = data[['zero', 'cdh60_temp']].max(axis=1)
data['cdh60sqr'] = data['cdh60']**2
del data['cdh60_temp']

# HDH 
data['hdh60_temp'] =  data['tempf_avg'] -60
data['zero'] = 0 
data['hdh60'] = data[['zero', 'hdh60_temp']].max(axis=1)
data['hdh60sqr'] = data['hdh60']**2
del data['hdh60_temp']
del data['zero']

# Rolling average of CDH
data['cdh_3hrma'] = data.cdh60.rolling(3).mean()
data['cdh_24hrma'] = data.cdh60.rolling(24).mean()
data['cdh_weeklag'] = data.cdh60.rolling(168).mean()

# Rolling average of HDH
data['hdh_3hrma'] = data.hdh60.rolling(3).mean()
data['hdh_24hrma'] = data.hdh60.rolling(24).mean()
data['hdh_weeklag'] = data.hdh60.rolling(168).mean()

#Reset index
data.reset_index(inplace = True) # Dont use abbr and datetime as index (for merges)

#Remove obs with blank data
data.head()

abbr            datetime     mw         datetime_utc        date  hour  \
0  AZPS 2018-10-20 17:00:00 3707.0  2018-10-21 00:00:00  2018-10-20    17   
1  AZPS 2018-10-20 16:00:00 3586.0  2018-10-20 23:00:00  2018-10-20    16   
2  AZPS 2018-10-20 15:00:00 3395.0  2018-10-20 22:00:00  2018-10-20    15   
3  AZPS 2018-10-20 01:00:00 2608.0  2018-10-20 08:00:00  2018-10-20     1   
4  AZPS 2018-10-20 00:00:00 2737.0  2018-10-20 07:00:00  2018-10-20     0   

   tempf  year  month  dayofweek     ...       cdh60  cdh60sqr  hdh60  \
0   69.3  2018     10          5     ...         9.3      85.7    9.3   
1   67.1  2018     10          5     ...         7.1      49.8    9.3   
2   64.1  2018     10          5     ...         4.1      17.1    9.3   
3   71.3  2018     10          5     ...        11.3     127.4    9.3   
4   74.6  2018     10          5     ...        14.6     212.3    9.3   

   hdh60sqr  cdh_3hrma  cdh_24hrma  cdh_weeklag  hdh_3hrma  hdh_24hrma  \
0      85.7        nan         nan          nan        nan         nan   
1      85.7        nan         nan          nan        nan         nan   
2      85.7        6.8         nan          nan        9.3         nan   
3      85.7        7.5         nan          nan        9.3         nan   
4      85.7       10.0         nan          nan        9.3         nan   

   hdh_weeklag  
0          nan  
1          nan  
2          nan  
3          nan  
4          nan  

[5 rows x 34 columns]

# Data Cleaning

In [13]:
# Identify and remove extreme high demand values by location
data = data.join(data.groupby('abbr')['mw'].quantile(0.95), 
                 on = 'abbr', rsuffix='_p95') 
data['ratio'] = data['mw'] / data['mw_p95']
data = data.loc[data['ratio'] <1.5 , :]
    

# Identify amd remove extreme low demand values by location
data = data.join(data.groupby('abbr')['mw'].quantile(0.05), 
                 on = 'abbr', rsuffix='_p05') 
data['ratio'] = data['mw'] / data['mw_p05']
data = data.loc[data['ratio'] > (1/1.5),:]  

In [14]:
# Remove missing values
data.dropna(how = 'any', inplace = True)
data.describe()

mw      hour     tempf      year     month  dayofweek  dayofyear  \
count 1100059.0 1100059.0 1100059.0 1100059.0 1100059.0  1100059.0  1100059.0   
mean     9237.2      11.6      59.9    2016.9       6.2        3.0      171.9   
std     18578.7       6.9      18.2       0.8       3.3        2.0      101.3   
min    -65426.0       0.0     -20.8    2016.0       1.0        0.0        1.0   
25%       968.0       6.0      47.3    2016.0       3.0        1.0       85.0   
50%      2476.0      12.0      60.8    2017.0       6.0        3.0      169.0   
75%      6080.0      18.0      74.0    2018.0       9.0        5.0      256.0   
max    152890.0      23.0     112.1    2018.0      12.0        6.0      366.0   

            mw_avg      mw_peak  tempf_peak    ...     hdh60sqr  cdh_3hrma  \
count    1100059.0    1100059.0   1100059.0    ...    1100059.0  1100059.0   
mean      113894.1     113894.1        70.7    ...        118.4        7.4   
std     10134724.8   10134724.8        17.8    ...        196.4        9.6   
min         -535.0       -535.0        -3.6    ...          0.0        0.0   
25%         1179.0       1179.0        58.2    ...          0.0        0.0   
50%         3019.0       3019.0        73.6    ...          2.6        1.2   
75%         7227.0       7227.0        84.9    ...        173.6       13.9   
max   1000001946.0 1000001946.0       112.1    ...       2044.4       51.7   

       cdh_24hrma  cdh_weeklag  hdh_3hrma  hdh_24hrma  hdh_weeklag    mw_p95  \
count   1100059.0    1100059.0  1100059.0   1100059.0    1100059.0 1100059.0   
mean          7.3          7.3        6.8         6.8          6.8   12808.1   
std           8.2          7.9        8.5         8.4          8.1   24587.4   
min           0.0          0.0        0.0         0.0          0.0      86.0   
25%           0.0          0.2        0.0         0.0          0.0    1500.0   
50%           4.1          4.4        1.7         1.9          2.7    3626.0   
75%          13.2         12.6       13.2        13.1         12.4    8092.6   
max          40.0         36.5       39.8        39.0         36.4  123577.3   

          ratio    mw_p05  
count 1100059.0 1100059.0  
mean        inf    6800.9  
std         nan   13794.6  
min         0.7     -34.0  
25%         1.2     655.0  
50%         1.4    1657.0  
75%         1.6    4706.2  
max         inf   69107.7  

[8 rows x 32 columns]

In [15]:
#Summarize usage by System
bindata = data.pivot_table(index ='abbr', values = 'mw', 
                           aggfunc = { "mw": [np.mean, np.std, min, max]})
bindata

max    mean      min     std
abbr                                  
AEC    1170.0   518.9    243.0   141.7
AECI   5279.0  2327.9   1143.0   641.4
AVA    2500.0  1346.7    748.0   287.1
AZPS   7558.0  3555.2   2023.0  1052.5
BANC   4763.0  2022.0   1288.0   530.9
BPAT  11827.0  6290.3   3659.0   978.2
CHPD    487.0   199.5    102.0    63.7
CISO  49899.0 26343.9  18068.0  5057.2
CPLE  14416.0  7085.5   3144.0  1760.4
DOPD    387.0   176.3     84.0    44.9
DUK   21608.0 12019.4   7067.0  2641.1
EPE    2026.0   976.0    441.0   270.1
ERCO  71193.0 40803.3  25146.0  9319.8
FPC   13152.0  6770.6   3203.0  1793.2
GCPD    982.0   570.4    362.0    79.5
GVL     500.0   236.7     99.0    66.1
IID    1081.0   430.5    155.0   184.5
IPCO   3849.0  1926.8    941.0   464.8
ISNE  25463.0 14110.6   9016.0  2571.9
JEA    3080.0  1527.2    655.0   396.0
LDWP   7095.0  3279.2   2117.0   759.0
LGEE   6845.0  4124.9   2522.0   844.5
MISO 119733.0 74962.1  50347.0 11904.5
NEVP   8525.0  4257.9   2747.0  1135.5
NSB     101.0    54.9     21.0    16.5
NWMT   1856.0  1291.3    729.0   172.4
NYIS  32076.0 18272.3  11831.0  3471.6
OVEC    146.0    73.2     14.0    17.3
PACE  10601.0  5493.6   2997.0   823.8
PACW   4386.0  2312.6   1133.0   418.5
PGE    4023.0  2338.4   1445.0   439.0
PJM  152890.0 91954.9  60522.0 16353.1
PNM    2608.0  1592.4   1090.0   255.8
PSCO   8634.0  4959.1   3411.0   844.9
PSEI   5504.0  3381.0   1861.0   638.3
SC     4980.0  2822.1   1353.0   626.3
SCEG   4807.0  2833.2   1355.0   622.2
SCL    1870.0  1105.0    530.0   202.5
SEC     -23.0  -738.4 -65426.0  5690.8
SOCO  45745.0 27385.1  15020.0  5795.8
SPA     151.0    77.6     38.0    15.9
SRP    8247.0  3362.5   2002.0  1063.4
SWPP  50500.0 30056.4  20051.0  5734.0
TEC    4347.0  2514.6   1212.0   644.3
TEPC   3799.0  1643.2    825.0   397.9
TIDC    653.0   307.1    183.0    84.2
TPWR    998.0   552.5    257.0   110.4
TVA   32511.0 18293.8  11134.0  3857.9
WACM   5152.0  2936.8   1669.0   368.1
WALC   2131.0  1062.8    500.0   226.6
WAUW    168.0    92.6     45.0    18.9

In [16]:
#Summarize Temperature by System
bindata = data.pivot_table(index ='abbr', values = 'tempf', 
                           aggfunc = { "tempf": [np.mean, np.std, min, max]})
bindata

max  mean   min  std
abbr                       
AEC   96.5  68.1  16.2 14.4
AECI  99.0  60.0  -5.0 18.9
AVA  100.3  46.9 -15.0 18.8
AZPS 112.1  69.3  26.5 17.7
BANC 101.5  59.7  23.8 14.5
BPAT  98.5  50.3  -0.2 16.9
CHPD  93.3  53.1  16.0 13.3
CISO 104.3  62.4  28.2 14.0
CPLE  96.4  64.2   9.4 16.5
DOPD  93.3  52.5  16.0 13.3
DUK   92.3  58.6  22.3 12.8
EPE  108.8  65.8   8.9 17.7
ERCO 102.3  66.3   9.7 16.5
FPC   93.9  76.0  27.7 10.3
GCPD  93.3  53.0  16.0 13.3
GVL   96.4  72.2  25.5 11.9
IID  101.9  70.2  39.0 12.1
IPCO 100.3  49.1 -15.2 19.6
ISNE  92.7  49.8 -12.6 19.0
JEA   96.8  69.5  20.9 13.7
LDWP 104.8  70.1  36.5 14.2
LGEE  97.5  60.9   1.5 18.2
MISO  96.3  53.5 -18.1 21.2
NEVP 106.0  61.9  16.0 18.0
NSB   95.0  75.5  28.3 10.6
NWMT 100.3  47.0 -16.1 20.4
NYIS  93.9  51.9  -8.9 19.2
OVEC  92.2  56.5  -2.8 17.5
PACE  98.0  53.8  -6.9 19.8
PACW 100.3  55.5  20.5 12.4
PGE   99.2  54.9  21.5 11.8
PJM   93.9  54.2  -4.0 19.6
PNM  100.5  56.0  -0.5 18.9
PSCO  94.8  47.8 -19.0 19.8
PSEI  94.2  53.6  21.8 11.0
SC    96.2  73.2  30.3 11.3
SCEG  96.2  72.2  23.9 11.9
SCL   94.2  53.7  21.8 11.0
SEC   91.7  69.9  40.0  9.6
SOCO  95.1  70.4  21.2 12.9
SPA   97.2  65.8  11.1 17.4
SRP  112.1  68.5  26.5 17.5
SWPP  96.8  62.5  15.1 15.4
TEC   94.6  73.8  27.2 10.6
TEPC 112.1  67.9  26.5 17.5
TIDC 104.3  62.4  28.2 14.0
TPWR  94.2  53.6  21.8 11.0
TVA   97.5  63.9   7.5 17.3
WACM  92.9  45.6 -20.8 19.1
WALC 105.8  68.4  31.5 15.1
WAUW 104.0  48.7 -15.0 22.8

# Exploratory Plot Data (for Tableau)

In [17]:
# A. Daily Peak versus Avg. Daily Temp

# 1. Main data summary
peakdata = data.pivot_table(index =['abbr', 'date'], 
                            values = ['mw', 'tempf'],
                            aggfunc = { "mw": max, "tempf": max})

peakdata = peakdata.add_suffix('_dailypeak')
peakdata.reset_index(inplace = True)

# 2. Add system info
peakdata = pd.merge(peakdata, systeminfo, on = 'abbr', how = 'inner')

# 3. Write to CSV for Tableau visualizations
peakdata.to_csv("../Data/Figures_peak_data.csv")


In [18]:
# B. Hourly load by temperature bins

#1. Create max temp bins
bins = list(range(5,105,5))
names = []
for bin in bins:
    lb = bin-5
    name = f'{lb} to {bin}F' 
    names.append(name)
del names[0]   
data["bins_maxtemp"] = pd.cut(data["tempf_peak"], bins, labels = names)


# 2. Main Summary
bindata = data.pivot_table(
        index = ['abbr', 'bins_maxtemp', 'hour'], values = 'mw', aggfunc = 'mean')

# 3. Add system info
bindata.reset_index(inplace = True)  # Needed for merge
bindata = pd.merge(bindata, systeminfo, on = 'abbr', how = 'inner')

# 4. Write to CSV for Tableau visualizations
bindata.to_csv("../Data/Figures_hourly_by_tempbins.csv")

In [19]:
#C. Most extreme grid demand days in U.S. 

#1. Aggregate US. Electric Demand
usa = data.pivot_table(index = ['datetime', 'date', 'hour'], values = 'mw', aggfunc = 'sum')
usa.reset_index(inplace = True) # Needed for merges

#2. Identify and Rank Peak Demand Days - keep top 20 
usapeaks = data.pivot_table(index = 'date', values = 'mw', aggfunc = 'max') #daily max by day
usapeaks['rank'] = usapeaks.mw.rank(method= 'first', ascending=False) # Rank days based on peak load
usapeaks = usapeaks.loc[(usapeaks['rank'] <= 20), :] # keep top 20 
del usapeaks['mw']
usapeaks.reset_index(inplace = True) # neeed for merger=s
usapeaks.head()

#3. Merge US peak day info to granular data - only keep top 20 days
usapeaks = pd.merge(usapeaks, data, how = 'inner', on = 'date')
usapeaks = usapeaks[['abbr',  'rank', 'datetime', 'date', 'hour','tempf']]
usapeaks.head()


# 3. Add system info
usapeaks = pd.merge(usapeaks, systeminfo, on = 'abbr', how = 'inner')

# 4. Write to CSV for Tableau visualizations
bindata.to_csv("../Data/Figures_top_20_days_us.csv")
usapeaks.head()

abbr  rank            datetime        date  hour  tempf   ID  \
0  AZPS  16.0 2016-07-22 23:00:00  2016-07-22    23  100.8  803   
1  AZPS  16.0 2016-07-22 22:00:00  2016-07-22    22  101.0  803   
2  AZPS  16.0 2016-07-22 21:00:00  2016-07-22    21  103.7  803   
3  AZPS  16.0 2016-07-22 20:00:00  2016-07-22    20  102.8  803   
4  AZPS  16.0 2016-07-22 19:00:00  2016-07-22    19  100.4  803   

                             NAME  PEAK_MONTH  AVAIL_CAP  TOTAL_CAP  \
0  ARIZONA PUBLIC SERVICE COMPANY         6.0    71475.0    90516.0   
1  ARIZONA PUBLIC SERVICE COMPANY         6.0    71475.0    90516.0   
2  ARIZONA PUBLIC SERVICE COMPANY         6.0    71475.0    90516.0   
3  ARIZONA PUBLIC SERVICE COMPANY         6.0    71475.0    90516.0   
4  ARIZONA PUBLIC SERVICE COMPANY         6.0    71475.0    90516.0   

   PEAK_LOAD  MIN_LOAD     SHAPE__Are    lat  lon  
0     7275.0    2260.0 417188000000.0 -111.6 34.3  
1     7275.0    2260.0 417188000000.0 -111.6 34.3  
2     7275.0    2260.0 417188000000.0 -111.6 34.3  
3     7275.0    2260.0 417188000000.0 -111.6 34.3  
4     7275.0    2260.0 417188000000.0 -111.6 34.3

# Prep Data for Model Fitting

In [20]:
# Use Pandas get_dummies to convert categorical data
weekdays = pd.get_dummies(data.dayofweek, prefix = 'dow')
data = data.join(weekdays)
data.head()
data.dropna(inplace = True)


In [22]:
# Change from Hour starting to hour ending  (Error for hour 0 )
data['hour'] = data['hour'] +1
#data.hour.value_counts(sort = False)

In [31]:
# Import Libraries
from sklearn.linear_model import LinearRegression
from sklearn.linear_model import ElasticNet
from sklearn.ensemble import RandomForestRegressor
from sklearn.svm import SVR
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import PolynomialFeatures
from sklearn.metrics import r2_score
import datetime


In [24]:
# FUNCTION IS DEFINED TO RUN FOR USER SPECIFIC MODEL, DAYTYPE (WEEKDAY/WEEKEND) AND HOUR
# RETURNS DATASET WITH ACTUAL V. PREDICTED

def runmodel(modeltype, location, weekday, hr): 

    # 1. Assign X (data) and y (target)
    hrdata  = data.loc[(data.abbr == location) & (data.hour == hr) & (data.weekday == weekday), :]
    X = hrdata[['mw_weeklag', 'cdh60', 'hdh60', 'cdh_24hrma', 'hdh_24hrma',
                'dow_0', 'dow_1', 'dow_2', 'dow_3', 'dow_4', 'dow_5', 'dow_6']]
    
    X = PolynomialFeatures(degree=2, include_bias=False).fit_transform(X)
    
    y = hrdata["mw"].values.reshape(-1, 1)
    #print(X.shape, y.shape)

   
    # 2. Split the data into training and testing
    X_train, X_test, y_train, y_test = train_test_split(X, y, random_state=777 )

    # 3. Create model and fit it to the scaled training data
    model = modeltype 
    model.fit(X_train, y_train)
    predictions = model.predict(X)
    r2_train = model.score(X_train, y_train)
    r2_test = model.score(X_test, y_test)

    print(f'Training Data R2: {r2_train}')
    print(f'Testing Data R2: {r2_test}')

    #4. Run model in full dataset and predict
    model.fit(X, y)
    predictions = model.predict(X)
    
    #5.  Add prediction back to main data frame
    mw =y.reshape(1, -1)
    predictions = predictions.reshape(1, -1)
    time = hrdata['datetime']

    mydict = { 
        "abbr" : location, 
        "model": str(modeltype),
        "datetime": time,
        "mw": mw[0],
        "predicted": predictions[0] 
    }
    newresults = pd.DataFrame(mydict)

    #5. Returns
    return newresults


In [25]:
# TEST FUNCTION USING ONE HOUR
m = LinearRegression()
s = "AZPS"
w = True
h = 17

results = runmodel(m,s, w, h)
# runmodel( 'AZPS', LinearRegression(), True, 16)
# runmodel('AZPS', ElasticNet(alpha=.05), True, 16)
# results = runmodel('AZPS', RandomForestRegressor(n_estimators = 50, random_state=7777, max_depth=4)
#          , True, 16)
#runmodel('AZPS', SVR(kernel = 'poly', degree = 2 )  # Takes too long, very little benefit
#         , True, 16)

results.head()

Training Data R2: 0.9427273858492081
Testing Data R2: 0.9155837601793646


abbr            datetime  \
177  AZPS 2018-10-06 16:00:00   
201  AZPS 2018-10-05 16:00:00   
225  AZPS 2018-10-04 16:00:00   
249  AZPS 2018-10-03 16:00:00   
273  AZPS 2018-10-02 16:00:00   

                                                 model     mw  predicted  
177  LinearRegression(copy_X=True, fit_intercept=Tr... 3310.0     3350.4  
201  LinearRegression(copy_X=True, fit_intercept=Tr... 3644.0     3764.4  
225  LinearRegression(copy_X=True, fit_intercept=Tr... 3797.0     3811.8  
249  LinearRegression(copy_X=True, fit_intercept=Tr... 3990.0     4238.5  
273  LinearRegression(copy_X=True, fit_intercept=Tr... 3479.0     4258.9

# Predictive Models

## Run for each model type, system, hour, and weekday/weekend

In [36]:
# RUN MODEL FOR EACH MODEL TYPE, SYSTEM, HOUR AND FOR WEEKDAY/WEEKEND 

#1. Set up lists
models = [LinearRegression(), ElasticNet(alpha=.05),
         RandomForestRegressor(n_estimators = 50, random_state=7777, max_depth=4)]

systems = systeminfo['abbr']
weekday = [True, False]
hours =  np.arange(24)+1

results = pd.DataFrame()

#2. Run Loops: 
for m in models : 
    for s in systems: 
        for w in weekday: 
            for h in hours:

                try: 
                    print(f'System {s} HOUR {h} WEEKDAY {w} - ' 
                          + str(datetime.datetime.now().time())) 
                    #hrdata = runmodel(LinearRegression(), s, w, h)
                    hrdata = runmodel(m, s, w, h)
                    results = results.append(hrdata)

                except: 
                    print(f'Oops! Model did not run: System {s} HOUR {h} WEEKDAY {w} - ' 
                          + str(datetime.datetime.now().time()))

#3. Save results data
results.to_csv("../Data/Modeling_results_predicted_v_actuals.csv")

System AZPS HOUR 1 WEEKDAY True - 11:31:30.068797
Training Data R2: 0.8702862763630644
Testing Data R2: 0.6903671435449956
System AZPS HOUR 2 WEEKDAY True - 11:31:30.222553
Training Data R2: 0.8626767926149148
Testing Data R2: 0.7453623808380475
System AZPS HOUR 3 WEEKDAY True - 11:31:30.326217
Training Data R2: 0.8433966144015943
Testing Data R2: 0.8570137515802541
System AZPS HOUR 4 WEEKDAY True - 11:31:30.493371
Training Data R2: 0.8089261393153959
Testing Data R2: 0.7695839495507059
System AZPS HOUR 5 WEEKDAY True - 11:31:30.640186
Training Data R2: 0.7792679523041772
Testing Data R2: 0.7502237895305778
System AZPS HOUR 6 WEEKDAY True - 11:31:30.757242
Training Data R2: 0.7416687165038589
Testing Data R2: 0.7030762418701328
System AZPS HOUR 7 WEEKDAY True - 11:31:30.883722
Training Data R2: 0.7049477856654526
Testing Data R2: 0.6125071893594833
System AZPS HOUR 8 WEEKDAY True - 11:31:31.015658
Training Data R2: 0.692841536257992
Testing Data R2: 0.6795509221605167
System AZPS HOUR 

Training Data R2: 0.7520733254985207
Testing Data R2: 0.7076545147834734
System AECI HOUR 20 WEEKDAY True - 11:31:40.777451
Training Data R2: 0.7254239088498886
Testing Data R2: 0.6930710409625771
System AECI HOUR 21 WEEKDAY True - 11:31:40.927736
Training Data R2: 0.7055385143376056
Testing Data R2: 0.5953294133402176
System AECI HOUR 22 WEEKDAY True - 11:31:41.087944
Training Data R2: 0.6850455520376771
Testing Data R2: 0.6673576630954555
System AECI HOUR 23 WEEKDAY True - 11:31:41.229801
Training Data R2: 0.6763490163486947
Testing Data R2: 0.6508846295137989
System AECI HOUR 24 WEEKDAY True - 11:31:41.375129
Training Data R2: 0.6571448159904485
Testing Data R2: 0.634746114274672
System AECI HOUR 1 WEEKDAY False - 11:31:41.529882
Training Data R2: 0.5565460373335629
Testing Data R2: 0.5560792691554215
System AECI HOUR 2 WEEKDAY False - 11:31:41.684137
Training Data R2: 0.5356519933273152
Testing Data R2: 0.5277415937730028
System AECI HOUR 3 WEEKDAY False - 11:31:41.825994
Training 

Training Data R2: 0.7926921049030653
Testing Data R2: 0.8217729928508755
System AVA HOUR 15 WEEKDAY False - 11:31:52.109079
Training Data R2: 0.7928716354123669
Testing Data R2: 0.7919319242435182
System AVA HOUR 16 WEEKDAY False - 11:31:52.270774
Training Data R2: 0.7877792529481537
Testing Data R2: 0.7558649986428403
System AVA HOUR 17 WEEKDAY False - 11:31:52.478600
Training Data R2: 0.7817439122824827
Testing Data R2: 0.7411881666507267
System AVA HOUR 18 WEEKDAY False - 11:31:52.617974
Training Data R2: 0.8113599371226764
Testing Data R2: 0.6869501669005199
System AVA HOUR 19 WEEKDAY False - 11:31:52.784632
Training Data R2: 0.8129093629954988
Testing Data R2: 0.6441531026803584
System AVA HOUR 20 WEEKDAY False - 11:31:52.933929
Training Data R2: 0.8256581073298344
Testing Data R2: 0.7270421225912924
System AVA HOUR 21 WEEKDAY False - 11:31:53.107032
Training Data R2: 0.8287030472754711
Testing Data R2: 0.7548536862525631
System AVA HOUR 22 WEEKDAY False - 11:31:53.286088
Training

Training Data R2: 0.7146222114763858
Testing Data R2: 0.5944855213181881
System BPAT HOUR 10 WEEKDAY True - 11:32:05.096359
Training Data R2: 0.7097636971693096
Testing Data R2: 0.5999959853408077
System BPAT HOUR 11 WEEKDAY True - 11:32:05.249623
Training Data R2: 0.681958360999624
Testing Data R2: 0.6597175784909051
System BPAT HOUR 12 WEEKDAY True - 11:32:05.419752
Training Data R2: 0.6791878951933032
Testing Data R2: 0.6005003314267146
System BPAT HOUR 13 WEEKDAY True - 11:32:05.596824
Training Data R2: 0.6785936129579393
Testing Data R2: 0.5453503307301477
System BPAT HOUR 14 WEEKDAY True - 11:32:05.762488
Training Data R2: 0.6595938111701631
Testing Data R2: 0.5293784287004166
System BPAT HOUR 15 WEEKDAY True - 11:32:05.930632
Training Data R2: 0.6264885095197467
Testing Data R2: 0.6212207454924442
System BPAT HOUR 16 WEEKDAY True - 11:32:06.102249
Training Data R2: 0.6301839020675939
Testing Data R2: 0.5534244738471777
System BPAT HOUR 17 WEEKDAY True - 11:32:06.260472
Training 

Training Data R2: 0.8486872160261568
Testing Data R2: 0.8128460265974299
System CISO HOUR 6 WEEKDAY False - 11:32:17.200264
Training Data R2: 0.8286720798090825
Testing Data R2: 0.827674775995961
System CISO HOUR 7 WEEKDAY False - 11:32:17.350551
Training Data R2: 0.8065639175239978
Testing Data R2: 0.749621346744934
System CISO HOUR 8 WEEKDAY False - 11:32:17.521175
Training Data R2: 0.808642143253995
Testing Data R2: 0.8104993200650641
System CISO HOUR 9 WEEKDAY False - 11:32:17.692792
Training Data R2: 0.8594139340154845
Testing Data R2: 0.6951839761682488
System CISO HOUR 10 WEEKDAY False - 11:32:17.860440
Training Data R2: 0.8456147332737285
Testing Data R2: 0.8115655376308383
System CISO HOUR 11 WEEKDAY False - 11:32:18.012217
Training Data R2: 0.8388106230904214
Testing Data R2: 0.8610873583627064
System CISO HOUR 12 WEEKDAY False - 11:32:18.176889
Training Data R2: 0.8537355538307978
Testing Data R2: 0.7833259471951284
System CISO HOUR 13 WEEKDAY False - 11:32:18.325193
Trainin

...

Training Data R2: 0.7968533008921299
Testing Data R2: 0.5708860638952852
System WAUW HOUR 23 WEEKDAY False - 12:52:11.944926


C:\Users\bodej\AppData\Local\conda\conda\envs\PythonData\lib\site-packages\ipykernel_launcher.py:22: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().
C:\Users\bodej\AppData\Local\conda\conda\envs\PythonData\lib\site-packages\ipykernel_launcher.py:31: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().


Training Data R2: 0.798701449014225
Testing Data R2: 0.6593185787579365
System WAUW HOUR 24 WEEKDAY False - 12:52:12.923009


C:\Users\bodej\AppData\Local\conda\conda\envs\PythonData\lib\site-packages\ipykernel_launcher.py:22: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().
C:\Users\bodej\AppData\Local\conda\conda\envs\PythonData\lib\site-packages\ipykernel_launcher.py:31: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().


Training Data R2: 0.80134127451932
Testing Data R2: 0.650151544827049


In [65]:
results.head()

Unnamed: 0  abbr             datetime  \
0         193  AZPS  2018-10-06 00:00:00   
1         217  AZPS  2018-10-05 00:00:00   
2         241  AZPS  2018-10-04 00:00:00   
3         265  AZPS  2018-10-03 00:00:00   
4         289  AZPS  2018-10-02 00:00:00   

                                               model     mw  predicted  
0  LinearRegression(copy_X=True, fit_intercept=Tr... 2911.0     2902.5  
1  LinearRegression(copy_X=True, fit_intercept=Tr... 3026.0     2950.7  
2  LinearRegression(copy_X=True, fit_intercept=Tr... 3233.0     3221.7  
3  LinearRegression(copy_X=True, fit_intercept=Tr... 3057.0     3356.3  
4  LinearRegression(copy_X=True, fit_intercept=Tr... 3131.0     3049.7